In [1]:
import numpy as np

import pandas as pd

from datetime import datetime

from bokeh.io import output_notebook, vform
from bokeh.plotting import figure, show
from bokeh.models import ColumnDataSource, HoverTool, CustomJS
from bokeh.models.widgets import Select

In [2]:
output_notebook()

Loading BokehJS ...

# All the equities on NASDAQ between 2008 and 2015

We take the prices of those equities, run t-SNE to project it to 2D, and visualize as below

In [3]:
data_file = 'nasdaq_indices_transposed_tsne_2dims.csv'
label_file = 'nasdaq_indices_transposed_labels.csv'

data = np.loadtxt(data_file, delimiter='\t')
labels = np.loadtxt(label_file, dtype=str)
assert data.shape[0] == labels.shape[0]

In [4]:
p = figure(width=800, height=800, tools="pan,wheel_zoom,box_zoom,reset,resize", 
           toolbar_location='above', title='NASDAQ indices 2008-2015')

source = ColumnDataSource(data=dict(x=data[:, 0], y=data[:, 1], label=[x[12:] for x in labels]))
hover = HoverTool(tooltips=[("(x,y)", "($x, $y)"), ("Symbol", " @label")])
p.circle('x', 'y', color='olive', size=10, alpha=0.4, hover_color='olive', hover_alpha=1.0, source=source)
p.add_tools(hover)

show(p)


# Price over time
We display the original time series of the price of equities in this section.

In [5]:
all_equities = pd.read_csv('nasdaq_indices_processed.csv')
idx = [datetime.strptime(x, '%Y-%m-%d') for x in all_equities.Date]
ALL_SYMBOLS = [x[12:] for x in all_equities.columns[1:]]

price_data = dict(x=idx, y=all_equities.loc[:, 'Close_YAHOO_INDEX_XOI'], date=all_equities.Date)
for c in ALL_SYMBOLS:
    price_data[c] = all_equities.loc[:, 'Close_YAHOO_' + c]

In [8]:
source2 = ColumnDataSource(data=price_data)

symbol_select_callback = CustomJS(args=dict(source=source2), code="""
        var data = source.get('data');
        var s = cb_obj.get('value');
        x = data['x'];
        y = data['y'];
        p = data[s];
        for (i = 0; i < x.length; i++) {
            y[i] = p[i];
        }
        source.trigger('change');
    """)
    
symbol_select = Select(title="Symbol:", value="INDEX_XOI", options=ALL_SYMBOLS, 
                      callback=symbol_select_callback)

# create a new plot with a datetime axis type
p2 = figure(width=800, height=450, x_axis_type="datetime", title='Stock index 2008-2015')

hover2 = HoverTool(tooltips=[("On", "@date"), ("Price", "$y")])
p2.line('x', 'y', color='navy', alpha=0.5, source=source2)
p2.add_tools(hover2)

show(vform(symbol_select, p2))


# Play with it yourself

Feel free to fork [my repo](https://github.com/phvu/misc/blob/master/stock_crawler/) and explore the data.